# Yolo Analysis

In [106]:
from functions import *

In [107]:
get_ipython().run_line_magic('load_ext', 'watermark')
get_ipython().run_line_magic('watermark', '-a "Silvan Zahno" -d -v -iv -m -h')

The watermark extension is already loaded. To reload it, use:
  %reload_ext watermark
platform    1.0.8
json        2.0.9
numpy       1.19.1
cv2.cv2     4.4.0
ctypes      1.1.0
logging     0.5.1.2
csv         1.0
pandas      1.1.3
PIL.Image   8.0.0
re          2.2.1
Silvan Zahno 2021-05-02 

CPython 3.6.5
IPython 5.8.0

compiler   : MSC v.1900 64 bit (AMD64)
system     : Windows
release    : 10
machine    : AMD64
processor  : Intel64 Family 6 Model 126 Stepping 5, GenuineIntel
CPU cores  : 8
interpreter: 64bit
host name  : zell


## Create Log Module

In [108]:
# Create log modules
handler = createHandler(dev_mode, LOG_PATH, "yolo_analysis")
log = createLogger(__name__)

In [109]:
log.debug(WEBCAM_PATH)
log.debug(OUT_PATH)
log.debug(DETECTION_PATH)
log.debug(TIMELOGS_PATH)
log.debug(LOG_PATH)

## Get Timelog files

In [110]:
files = sorted(getListOfFiles(TIMELOGS_PATH, False, True))
out = "## Files found:" + os.linesep + os.linesep
if verbose:
  for file in files:
    out += "* {}".format(file) + os.linesep
print(Markdown(out))

In [111]:
# get all pynq files
files_list = []
for file in files:
  filesplit = os.path.split(file)
  match = re.match(r"(\d{8})(\d{4})-(.+)-(.+.csv)", filesplit[1])
  if match is not None:
    match = match.groups()
    files_list.append([match[0], match[1], match[2], file])

table = Table(title="Files identified")

table.add_column("Date", justify="right", style="cyan", no_wrap=True)
table.add_column("Time", justify="right", style="magenta", no_wrap=True)
table.add_column("Device", justify="right", style="green", no_wrap=True)
table.add_column("Path", justify="left", style="green", no_wrap=True)

for file in files_list:
  table.add_row(file[0], file[1], file[2], os.path.split(file[3])[1])

print(table)  

In [112]:
print(len(files_list))
print(files_list)

## Create Dataframe

In [113]:
dfs = []

# Create dataframes
for file_list in files_list:
  dfs.append(pd.read_csv(file_list[3]))
  dfs[-1]['device'] = file_list[2]
  dfs[-1].rename(columns={'text': 'action'}, inplace=True)
  
# Filter out type 0
for i in range(len(dfs)):
  dfs[i] = dfs[i][dfs[i].type != 0]
  dfs[i]['time'] = pd.to_timedelta(dfs[i]['time'])
  dfs[i].drop(['type'], axis=1, inplace=True)

# Conatenate all dataframes
df = pd.concat(dfs)

# Make devices human readable
for device in hr_devices:
  df['device'] = df['device'].str.replace(device, hr_devices[device])

pd.options.display.max_rows = None
display(df)

index                   time                        action                device
2         0 0 days 00:00:06.997333                    Setup YOLO  Xilinx PYNQ-Z1 SW/HW
5         0 0 days 00:00:00.398230                 Image Loading  Xilinx PYNQ-Z1 SW/HW
8         0 0 days 00:00:00.570836    Apply YOLO SW Conv Layer 0  Xilinx PYNQ-Z1 SW/HW
11        0 0 days 00:00:00.982011  Apply YOLO HW Conv Layer 1-7  Xilinx PYNQ-Z1 SW/HW
14        0 0 days 00:00:00.097420    Apply YOLO SW Conv Layer 8  Xilinx PYNQ-Z1 SW/HW
17        0 0 days 00:00:02.043572          Draw Detection Boxes  Xilinx PYNQ-Z1 SW/HW
20        1 0 days 00:00:00.371652                 Image Loading  Xilinx PYNQ-Z1 SW/HW
23        1 0 days 00:00:00.541674    Apply YOLO SW Conv Layer 0  Xilinx PYNQ-Z1 SW/HW
26        1 0 days 00:00:00.956380  Apply YOLO HW Conv Layer 1-7  Xilinx PYNQ-Z1 SW/HW
29        1 0 days 00:00:00.094354    Apply YOLO SW Conv Layer 8  Xilinx PYNQ-Z1 SW/HW
32        1 0 days 00:00:01.487933          Draw Detection Boxes  Xilinx PYNQ-Z1 SW/HW
35        2 0 days 00:00:00.372129                 Image Loading  Xilinx PYNQ-Z1 SW/HW
38        2 0 days 00:00:00.524701    Apply YOLO SW Conv Layer 0  Xilinx PYNQ-Z1 SW/HW
41        2 0 days 00:00:00.955060  Apply YOLO HW Conv Layer 1-7  Xilinx PYNQ-Z1 SW/HW
44        2 0 days 00:00:00.105263    Apply YOLO SW Conv Layer 8  Xilinx PYNQ-Z1 SW/HW
47        2 0 days 00:00:01.510158          Draw Detection Boxes  Xilinx PYNQ-Z1 SW/HW
50        3 0 days 00:00:00.369653                 Image Loading  Xilinx PYNQ-Z1 SW/HW
53        3 0 days 00:00:00.534894    Apply YOLO SW Conv Layer 0  Xilinx PYNQ-Z1 SW/HW
56        3 0 days 00:00:00.950729  Apply YOLO HW Conv Layer 1-7  Xilinx PYNQ-Z1 SW/HW
59        3 0 days 00:00:00.094568    Apply YOLO SW Conv Layer 8  Xilinx PYNQ-Z1 SW/HW
62        3 0 days 00:00:01.484368          Draw Detection Boxes  Xilinx PYNQ-Z1 SW/HW
65        4 0 days 00:00:00.370422                 Image Loading  Xilinx PYNQ-Z1 SW/HW
68        4 0 days 00:00:00.549187    Apply YOLO SW Conv Layer 0  Xilinx PYNQ-Z1 SW/HW
71        4 0 days 00:00:00.952487  Apply YOLO HW Conv Layer 1-7  Xilinx PYNQ-Z1 SW/HW
74        4 0 days 00:00:00.094992    Apply YOLO SW Conv Layer 8  Xilinx PYNQ-Z1 SW/HW
77        4 0 days 00:00:01.477636          Draw Detection Boxes  Xilinx PYNQ-Z1 SW/HW
80        5 0 days 00:00:00.392084                 Image Loading  Xilinx PYNQ-Z1 SW/HW
83        5 0 days 00:00:00.578805    Apply YOLO SW Conv Layer 0  Xilinx PYNQ-Z1 SW/HW
86        5 0 days 00:00:00.952237  Apply YOLO HW Conv Layer 1-7  Xilinx PYNQ-Z1 SW/HW
89        5 0 days 00:00:00.094392    Apply YOLO SW Conv Layer 8  Xilinx PYNQ-Z1 SW/HW
92        5 0 days 00:00:01.468032          Draw Detection Boxes  Xilinx PYNQ-Z1 SW/HW
95        6 0 days 00:00:00.373322                 Image Loading  Xilinx PYNQ-Z1 SW/HW
98        6 0 days 00:00:00.536070    Apply YOLO SW Conv Layer 0  Xilinx PYNQ-Z1 SW/HW
101       6 0 days 00:00:00.949785  Apply YOLO HW Conv Layer 1-7  Xilinx PYNQ-Z1 SW/HW
104       6 0 days 00:00:00.094999    Apply YOLO SW Conv Layer 8  Xilinx PYNQ-Z1 SW/HW
107       6 0 days 00:00:01.499363          Draw Detection Boxes  Xilinx PYNQ-Z1 SW/HW
110       7 0 days 00:00:00.372955                 Image Loading  Xilinx PYNQ-Z1 SW/HW
113       7 0 days 00:00:00.542319    Apply YOLO SW Conv Layer 0  Xilinx PYNQ-Z1 SW/HW
116       7 0 days 00:00:00.951279  Apply YOLO HW Conv Layer 1-7  Xilinx PYNQ-Z1 SW/HW
119       7 0 days 00:00:00.094526    Apply YOLO SW Conv Layer 8  Xilinx PYNQ-Z1 SW/HW
122       7 0 days 00:00:01.467134          Draw Detection Boxes  Xilinx PYNQ-Z1 SW/HW
125       8 0 days 00:00:00.374438                 Image Loading  Xilinx PYNQ-Z1 SW/HW
128       8 0 days 00:00:00.542279    Apply YOLO SW Conv Layer 0  Xilinx PYNQ-Z1 SW/HW
131       8 0 days 00:00:00.950272  Apply YOLO HW Conv Layer 1-7  Xilinx PYNQ-Z1 SW/HW
134       8 0 days 00:00:00.094570    Apply YOLO SW Conv Layer 8  Xilinx PYNQ-Z1 SW/HW
137 

## Plot Raw data

In [114]:
title = "Raw YOLO CNN Speed Comparison"
# Workaround 
df_tmp = df.copy()
df_tmp['time'] = df_tmp['time'] + pd.to_datetime('1970/01/01')
fig = px.violin(df_tmp, y="time", x="action", color="device", box=True, points="all", hover_data=df_tmp.columns, title=title)
fig.show()
#fname = PLOT_PATH + os.sep + time.strftime("%Y%m%d%H%M", time.localtime()) + "_" + title + PLOT_EXT
fname = (PLOT_PATH + os.sep + title + PLOT_EXT).replace(' ', '_').lower()
fig.write_image(fname)


## Calculate Average Times

In [117]:
columns = { hr_devices['zell-sw'] : { "Setup": ["Setup YOLO"],
                                      "Image Loading": ["Image Loading"],
                                      "YOLO CNN": ["Apply YOLO SW Conv Layers"],
                                      "Detection Box": ["Draw Detection Boxes"]},
            hr_devices['pynq-sw'] : { "Setup": ["Setup YOLO"],
                                      "Image Loading": ["Image Loading"],
                                      "YOLO CNN": ["Apply YOLO HW Conv Layer 1-7"],
                                      #"YOLO CNN": ["Apply YOLO SW Conv Layers"],
                                      "Detection Box": ["Draw Detection Boxes"]},
            hr_devices['pynq-hw'] : { "Setup": ["Setup YOLO"],
                                      "Image Loading": ["Image Loading"],
                                      #"YOLO CNN": ["Apply YOLO SW Conv Layer 0", "Apply YOLO HW Conv Layer 1-7", "Apply YOLO SW Conv Layer 8"],
                                      "YOLO CNN": ["Apply YOLO HW Conv Layer 1-7"],
                                      "Detection Box": ["Draw Detection Boxes"]}

}

df_sum = pd.DataFrame(columns=['device', "index", "time", "action"])
for device in df['device'].unique():             # loop through device
  for index in df['index'].unique():             # loop through recordings
    for actiontype in columns[device]:           # loop through actiontype
      x = timedelta(seconds = 0)
      for action in columns[device][actiontype]: # loop through actions
        query = df.query('device == @device & index == @index & action == @action')
        if len(query) > 0:
          x = x + df.query('device == @device & index == @index & action == @action')['time'].iloc[0]
      if x != timedelta(seconds = 0):
        df_sum = df_sum.append({'device': device, 'index': index, 'action': actiontype, 'time': x}, ignore_index=True)

display(df_sum)

        

device index                   time         action
0     Xilinx PYNQ-Z1 SW/HW     0 0 days 00:00:06.997333          Setup
1     Xilinx PYNQ-Z1 SW/HW     0 0 days 00:00:00.398230  Image Loading
2     Xilinx PYNQ-Z1 SW/HW     0 0 days 00:00:00.982011       YOLO CNN
3     Xilinx PYNQ-Z1 SW/HW     0 0 days 00:00:02.043572  Detection Box
4     Xilinx PYNQ-Z1 SW/HW     1 0 days 00:00:00.371652  Image Loading
5     Xilinx PYNQ-Z1 SW/HW     1 0 days 00:00:00.956380       YOLO CNN
6     Xilinx PYNQ-Z1 SW/HW     1 0 days 00:00:01.487933  Detection Box
7     Xilinx PYNQ-Z1 SW/HW     2 0 days 00:00:00.372129  Image Loading
8     Xilinx PYNQ-Z1 SW/HW     2 0 days 00:00:00.955060       YOLO CNN
9     Xilinx PYNQ-Z1 SW/HW     2 0 days 00:00:01.510158  Detection Box
10    Xilinx PYNQ-Z1 SW/HW     3 0 days 00:00:00.369653  Image Loading
11    Xilinx PYNQ-Z1 SW/HW     3 0 days 00:00:00.950729       YOLO CNN
12    Xilinx PYNQ-Z1 SW/HW     3 0 days 00:00:01.484368  Detection Box
13    Xilinx PYNQ-Z1 SW/HW     4 0 days 00:00:00.370422  Image Loading
14    Xilinx PYNQ-Z1 SW/HW     4 0 days 00:00:00.952487       YOLO CNN
15    Xilinx PYNQ-Z1 SW/HW     4 0 days 00:00:01.477636  Detection Box
16    Xilinx PYNQ-Z1 SW/HW     5 0 days 00:00:00.392084  Image Loading
17    Xilinx PYNQ-Z1 SW/HW     5 0 days 00:00:00.952237       YOLO CNN
18    Xilinx PYNQ-Z1 SW/HW     5 0 days 00:00:01.468032  Detection Box
19    Xilinx PYNQ-Z1 SW/HW     6 0 days 00:00:00.373322  Image Loading
20    Xilinx PYNQ-Z1 SW/HW     6 0 days 00:00:00.949785       YOLO CNN
21    Xilinx PYNQ-Z1 SW/HW     6 0 days 00:00:01.499363  Detection Box
22    Xilinx PYNQ-Z1 SW/HW     7 0 days 00:00:00.372955  Image Loading
23    Xilinx PYNQ-Z1 SW/HW     7 0 days 00:00:00.951279       YOLO CNN
24    Xilinx PYNQ-Z1 SW/HW     7 0 days 00:00:01.467134  Detection Box
25    Xilinx PYNQ-Z1 SW/HW     8 0 days 00:00:00.374438  Image Loading
26    Xilinx PYNQ-Z1 SW/HW     8 0 days 00:00:00.950272       YOLO CNN
27    Xilinx PYNQ-Z1 SW/HW     8 0 days 00:00:01.469153  Detection Box
28    Xilinx PYNQ-Z1 SW/HW     9 0 days 00:00:00.374320  Image Loading
29    Xilinx PYNQ-Z1 SW/HW     9 0 days 00:00:00.972134       YOLO CNN
30    Xilinx PYNQ-Z1 SW/HW     9 0 days 00:00:01.470734  Detection Box
31    Xilinx PYNQ-Z1 SW/HW    10 0 days 00:00:00.376418  Image Loading
32    Xilinx PYNQ-Z1 SW/HW    10 0 days 00:00:00.951060       YOLO CNN
33    Xilinx PYNQ-Z1 SW/HW    10 0 days 00:00:01.471513  Detection Box
34    Xilinx PYNQ-Z1 SW/HW    11 0 days 00:00:00.375258  Image Loading
35    Xilinx PYNQ-Z1 SW/HW    11 0 days 00:00:00.951818       YOLO CNN
36    Xilinx PYNQ-Z1 SW/HW    11 0 days 00:00:01.466211  Detection Box
37    Xilinx PYNQ-Z1 SW/HW    12 0 days 00:00:00.394738  Image Loading
38    Xilinx PYNQ-Z1 SW/HW    12 0 days 00:00:00.951410       YOLO CNN
39    Xilinx PYNQ-Z1 SW/HW    12 0 days 00:00:01.514333  Detection Box
40    Xilinx PYNQ-Z1 SW/HW    13 0 days 00:00:00.373527  Image Loading
41    Xilinx PYNQ-Z1 SW/HW    13 0 days 00:00:00.955476       YOLO CNN
42    Xilinx PYNQ-Z1 SW/HW    13 0 days 00:00:01.468986  Detection Box
43    Xilinx PYNQ-Z1 SW/HW    14 0 days 00:00:00.375016  Image Loading
44    Xilinx PYNQ-Z1 SW/HW    14 0 days 00:00:00.956233       YOLO CNN
45    Xilinx PYNQ-Z1 SW/HW    14 0 days 00:00:01.469899  Detection Box
46    Xilinx PYNQ-Z1 SW/HW    15 0 days 00:00:00.400976  Image Loading
47    Xilinx PYNQ-Z1 SW/HW    15 0 days 00:00:00.955658       YOLO CNN
48    Xilinx PYNQ-Z1 SW/HW    15 0 days 00:00:01.463014  Detection Box
49    Xilinx PYNQ-Z1 SW/HW    16 0 days 00:00:00.376588  Image Loading
50    Xilinx PYNQ-Z1 SW/HW    16 0 days 00:00:00.955912       YOLO CNN
51    Xilinx PYNQ-Z1 SW/HW    16 0 days 00:00:01.437660  Detection Box
52    Xilinx PYNQ-Z1 SW/HW    17 0 days 00:00:00.374612  Image Loading
53    Xilinx PYNQ-Z1 SW/HW    17 0 days 00:00:00.950719       YOLO CNN
54    Xilinx PYNQ-Z1 SW/HW    17 0 days 00:00:01.462632  Detection Box
55    Xilinx PYNQ-Z1 SW/HW    18 0 days 00:0

In [118]:
title = "YOLO CNN Speed Comparison FPGA vs Software"
df_tmp = df_sum.copy()
df_tmp['time'] = df_tmp['time'] + pd.to_datetime('1970/01/01')
fig = px.violin(df_tmp, y="time", x="action", color="device", box=True, points="all", hover_data=df_tmp.columns,  title=title)
fig.show()
#fname = PLOT_PATH + os.sep + time.strftime("%Y%m%d%H%M", time.localtime()) + "_" + title + PLOT_EXT
fname = (PLOT_PATH + os.sep + title + PLOT_EXT).replace(' ', '_').lower()
fig.write_image(fname)
print(fname)